# AbXtract - Comprehensive Testing and Examples

This notebook demonstrates the complete functionality of the AbXtract package for antibody descriptor calculations.

## 📚 Table of Contents
1. [Setup and Imports](#setup)
2. [Configuration Testing](#config)
3. [Individual Calculator Testing](#individual)
4. [Sequence-based Analysis](#sequence)
5. [Structure-based Analysis](#structure)
6. [Combined Analysis](#combined)
7. [Batch Processing](#batch)
8. [Visualization Examples](#viz)
9. [Export and Import](#export)

## 1. Setup and Imports {#setup}

Let's start by importing all necessary modules and setting up the environment.

In [1]:
import sys
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pathlib import Path
import warnings
warnings.filterwarnings('ignore')

# Set up matplotlib
plt.style.use('default')
sns.set_palette("husl")

print("📦 Basic imports successful")

📦 Basic imports successful


In [2]:
# Check what's actually available
import sys
print("Python path:")
for p in sys.path:
    print(f"  {p}")

# Check if AbXtract directory is accessible
import os
abxtract_path = "/home/HX46_FR5/repo_perso/AbXtract"
print(f"\nAbXtract path exists: {os.path.exists(abxtract_path)}")
print(f"AbXtract path in sys.path: {abxtract_path in sys.path}")

Python path:
  /opt/conda/envs/abxtract/lib/python39.zip
  /opt/conda/envs/abxtract/lib/python3.9
  /opt/conda/envs/abxtract/lib/python3.9/lib-dynload
  
  /opt/conda/envs/abxtract/lib/python3.9/site-packages

AbXtract path exists: True
AbXtract path in sys.path: False


In [3]:
import sys
import os
sys.path.insert(0, '/home/HX46_FR5/repo_perso/AbXtract')

# Now try the imports
try:
    from AbXtract import *
    print("✅ AbXtract imported successfully!")
except ImportError as e:
    print(f"❌ Still having issues: {e}")

✅ AbXtract imported successfully!


In [4]:
# Import AbXtract modules
try:
    from AbXtract import AntibodyDescriptorCalculator, Config, load_config
    from AbXtract.sequence import (
        SequenceLiabilityAnalyzer,
        BashourDescriptorCalculator,
        PeptideDescriptorCalculator,
        AntibodyNumbering
    )
    from AbXtract.structure import (
        SASACalculator,
        ChargeAnalyzer,
        DSSPAnalyzer,
        PropkaAnalyzer,
        ArpeggioAnalyzer
    )
    from AbXtract.utils import (
        read_fasta,
        write_fasta,
        parse_sequence,
        validate_sequence
    )
    
    print("🚀 AbXtract imports successful!")
    
except ImportError as e:
    print(f"❌ Import error: {e}")
    print("Please make sure AbXtract is installed and in your Python path")
    sys.exit(1)

🚀 AbXtract imports successful!


In [5]:
# Set up test data paths
BASE_DIR = Path.cwd() # pass to ../ chmod ../
DATA_DIR = BASE_DIR / "data" / "test"
DATA_DIR.mkdir(parents=True, exist_ok=True)

# Define test file paths
FASTA_FILE = DATA_DIR / "test_antibody.fasta"
PDB_FILE = DATA_DIR / "test.pdb"  # User will provide this
RESULTS_DIR = DATA_DIR / "results"
RESULTS_DIR.mkdir(exist_ok=True)

print(f"📁 Test data directory: {DATA_DIR}")
print(f"📁 Results directory: {RESULTS_DIR}")

📁 Test data directory: /home/HX46_FR5/repo_perso/AbXtract/examples/data/test
📁 Results directory: /home/HX46_FR5/repo_perso/AbXtract/examples/data/test/results


## 2. Configuration Testing {#config}

Test the configuration system and external tool availability.

In [6]:
# Test default configuration
config = Config()
print("🔧 Default Configuration:")
print(f"  Numbering scheme: {config.numbering_scheme}")
print(f"  pH: {config.pH}")
print(f"  Temperature: {config.temperature}°C")
print(f"  Output format: {config.output_format}")
print(f"  Verbose: {config.verbose}")

🔧 Default Configuration:
  Numbering scheme: imgt
  pH: 7.0
  Temperature: 25.0°C
  Output format: csv
  Verbose: True


In [7]:
# Check external tool availability
tool_status = config.check_external_tools()
print("🛠️ External Tool Status:")
for tool, available in tool_status.items():
    status = "✅" if available else "❌"
    print(f"  {tool}: {status}")

# Count available tools
available_count = sum(tool_status.values())
total_count = len(tool_status)
print(f"\n📊 {available_count}/{total_count} external tools available")

reduce not found at reduce


🛠️ External Tool Status:
  dssp: ✅
  propka: ✅
  arpeggio: ✅
  reduce: ❌
  muscle: ✅

📊 4/5 external tools available


In [8]:
# Test custom configuration
custom_config = Config.from_dict({
    'pH': 7.4,
    'numbering_scheme': 'kabat',
    'verbose': True,
    'calculate_dssp': tool_status.get('dssp', False),
    'calculate_propka': tool_status.get('propka', False),
    'calculate_arpeggio': tool_status.get('arpeggio', False)
})

print("🎛️ Custom Configuration created with optimal settings")
print(f"  DSSP enabled: {custom_config.calculate_dssp}")
print(f"  PROPKA enabled: {custom_config.calculate_propka}")
print(f"  Arpeggio enabled: {custom_config.calculate_arpeggio}")

🎛️ Custom Configuration created with optimal settings
  DSSP enabled: True
  PROPKA enabled: True
  Arpeggio enabled: True


## 3. Test Sequences Setup

Let's create our test sequences and save them to a FASTA file.

In [9]:
# Test antibody sequences (based on therapeutic antibodies)
# Heavy chain: Includes realistic VH domain + human IgG1 constant region
HEAVY_SEQUENCE = (
    "QVQLVQSGAEVKKPGASVKVSCKASGGTFSSYAISWVRQAPGQGLEWMG"
    "GIIPIFGTANYAQKFQGRVTITADESTSTAYMELSSLRSEDTAVYYCAR"
    "SHYGLDYWGQGTLVTVSSASTKGPSVFPLAPSSKSTSGGTAALGCLVKD"
    "YFPEPVTVSWNSGALTSGVHTFPAVLQSSGLYSLSSVVTVPSSSLGTQT"
    "YICNVNHKPSNTKVDKKVEPKSCDKTHTCPPCPAPELLGGPSVFLFPPK"
    "PKDTLMISRTPEVTCVVVDVSHEDPEVKFNWYVDGVEVHNAKTKPREEQ"
    "YASTYRVVSVLTVLHQDWLNGKEYKCKVSNKALPAPIEKTISKAKGQPR"
    "EPQVYTLPPSRDELTKNQVSLTCLVKGFYPSDIAVEWESNGQPENNYK"
    "TTPPVLDSDGSFFLYSKLTVDKSRWQQGNVFSCSVMHEALHNHYTQKS"
    "LSLSPGK"
)

# Light chain: Includes realistic VL domain + human kappa constant region  
LIGHT_SEQUENCE = (
    "DIQMTQSPSSLSASVGDRVTITCRASHSISSYLAWYQQKPGKAPKLLIY"
    "AASSLQSGVPSRFSGSGSGTDFTLTISSLQPEDFATYYCQQSYSTPLTF"
    "GGGTKVEIKRTVAAPSVFIFPPSDEQLKSGTASVVCLLNNFYPREAKV"
    "QWKVDNALQSGNSQESVTEQDSKDSTYSLSSTLTLSKADYEKHKVYAC"
    "EVTHQGLSSPVTKSFNRGEC"
)

print(f"🧬 Heavy chain length: {len(HEAVY_SEQUENCE)} aa")
print(f"🧬 Light chain length: {len(LIGHT_SEQUENCE)} aa")
print(f"🧬 Total antibody length: {len(HEAVY_SEQUENCE + LIGHT_SEQUENCE)} aa")

🧬 Heavy chain length: 446 aa
🧬 Light chain length: 214 aa
🧬 Total antibody length: 660 aa


In [10]:
# Validate sequences
heavy_valid, heavy_msg = validate_sequence(HEAVY_SEQUENCE)
light_valid, light_msg = validate_sequence(LIGHT_SEQUENCE)

print("✅ Sequence Validation:")
print(f"  Heavy chain: {'✅ Valid' if heavy_valid else '❌ Invalid - ' + heavy_msg}")
print(f"  Light chain: {'✅ Valid' if light_valid else '❌ Invalid - ' + light_msg}")

if not (heavy_valid and light_valid):
    raise ValueError("Test sequences are invalid!")

✅ Sequence Validation:
  Heavy chain: ✅ Valid
  Light chain: ✅ Valid


In [11]:
# Create FASTA file for testing
test_sequences = {
    "Test_Antibody_Heavy_Chain": HEAVY_SEQUENCE,
    "Test_Antibody_Light_Chain": LIGHT_SEQUENCE
}

write_fasta(test_sequences, FASTA_FILE)
print(f"💾 Test FASTA file created: {FASTA_FILE}")

# Verify we can read it back
loaded_sequences = read_fasta(FASTA_FILE)
print(f"📖 Loaded {len(loaded_sequences)} sequences from FASTA:")
for seq_id, seq in loaded_sequences.items():
    print(f"  {seq_id}: {len(seq)} aa")

💾 Test FASTA file created: /home/HX46_FR5/repo_perso/AbXtract/examples/data/test/test_antibody.fasta
📖 Loaded 2 sequences from FASTA:
  Test_Antibody_Heavy_Chain: 446 aa
  Test_Antibody_Light_Chain: 214 aa


## 4. Individual Calculator Testing {#individual}

Test each calculator module individually to ensure they work correctly.

In [12]:
# Test Liability Analyzer
print("🔍 Testing Sequence Liability Analyzer...")

liability_analyzer = SequenceLiabilityAnalyzer()
liability_results = liability_analyzer.analyze(
    heavy_sequence=HEAVY_SEQUENCE,
    light_sequence=LIGHT_SEQUENCE
)

print(f"  Found {liability_results['count']} liabilities")
print(f"  Total possible liabilities checked: {liability_results['total_possible']}")

if liability_results['liabilities']:
    print("\n  Detected liabilities:")
    for liability in liability_results['liabilities'][:5]:  # Show first 5
        print(f"    - {liability['name']} in chain {liability['chain']} at position {liability['start_position']}")
        print(f"      Sequence: {liability['sequence']}")
else:
    print("  ✅ No sequence liabilities detected")

🔍 Testing Sequence Liability Analyzer...
  Found 4 liabilities
  Total possible liabilities checked: 12

  Detected liabilities:
    - Met oxidation (M) in chain L at position [4, ' ']
      Sequence: M
    - Trp oxidation (W) in chain H at position [118, ' ']
      Sequence: W
    - Trp oxidation (W) in chain L at position [41, ' ']
      Sequence: W
    - Polyreactivity (RR VG VV VVV WW WWW WXW) in chain L at position [15, ' ']
      Sequence: VG


In [13]:
liability_results

{'liabilities': [{'name': 'Met oxidation (M)',
   'chain': 'L',
   'start_index': 3,
   'end_index': 3,
   'start_position': [4, ' '],
   'end_position': [4, ' '],
   'sequence': 'M',
   'region': ['cdrs', 'verniers']},
  {'name': 'Trp oxidation (W)',
   'chain': 'H',
   'start_index': 105,
   'end_index': 105,
   'start_position': [118, ' '],
   'end_position': [118, ' '],
   'sequence': 'W',
   'region': ['cdrs', 'verniers']},
  {'name': 'Trp oxidation (W)',
   'chain': 'L',
   'start_index': 34,
   'end_index': 34,
   'start_position': [41, ' '],
   'end_position': [41, ' '],
   'sequence': 'W',
   'region': ['cdrs', 'verniers']},
  {'name': 'Polyreactivity (RR VG VV VVV WW WWW WXW)',
   'chain': 'L',
   'start_index': 14,
   'end_index': 15,
   'start_position': [15, ' '],
   'end_position': [16, ' '],
   'sequence': 'VG',
   'region': ['fv']}],
 'count': 4,
 'total_possible': 12,
 'heavy_sequence': 'QVQLVQSGAEVKKPGASVKVSCKASGGTFSSYAISWVRQAPGQGLEWMGGIIPIFGTANYAQKFQGRVTITADESTSTAYME

In [14]:
# Test Bashour Descriptor Calculator
print("📊 Testing Bashour Descriptor Calculator...")

bashour_calc = BashourDescriptorCalculator()
bashour_results = bashour_calc.calculate({
    'Heavy': HEAVY_SEQUENCE,
    'Light': LIGHT_SEQUENCE
})

print(f"  Calculated {len(bashour_results.columns)} descriptors for {len(bashour_results)} chains")
print(f"  Columns: {list(bashour_results.columns[:10])}...")  # First 10 columns

import pandas as pd

# list of charge cols
charge_cols = [f"Charge_pH_{i}" for i in range(1, 15)]

# drop if they already exist
bashour_results = bashour_results.drop(columns=charge_cols, errors="ignore")

# expand the dictionary
charges_expanded = bashour_results["Charges (all pH values)"].apply(pd.Series)
charges_expanded.columns = [f"Charge_pH_{c}" for c in charges_expanded.columns]

# merge back
bashour_results = pd.concat([bashour_results.drop(columns=["Charges (all pH values)"]),
                             charges_expanded], axis=1)



📊 Testing Bashour Descriptor Calculator...
  Calculated 38 descriptors for 2 chains
  Columns: ['SeqID', 'Seq', 'Dataset', 'Molecular Weight', 'Seq Length', 'Average Residue Weight', 'pI', 'Charges (all pH values)', 'Charge_pH_1', 'Charge_pH_2']...

  Key descriptors:


SeqID                                                Seq   Dataset  \
0  Heavy  QVQLVQSGAEVKKPGASVKVSCKASGGTFSSYAISWVRQAPGQGLE...  Analysis   
1  Light  DIQMTQSPSSLSASVGDRVTITCRASHSISSYLAWYQQKPGKAPKL...  Analysis   

   Molecular Weight  Seq Length  Average Residue Weight        pI  \
0       48473.79784         446              108.685645  8.063751   
1       23173.78954         214              108.288736  7.590943   

   Molecular Extinction Coefficient  \
0                             72935   
1                             26150   

   Molecular Extinction Coefficient (Cysteine bridges)  \
0                                                625     
1                                                250     

   % Molecular Extinction Coefficient  ...  Charge_pH_5  Charge_pH_6  \
0                           15.046273  ...    18.091234    10.380759   
1                           11.284300  ...     5.469652     2.663232   

   Charge_pH_7  Charge_pH_8  Charge_pH_9  Charge_pH_10  Charge_pH_11  \
0     5.245623     0.449583    -7.152660    -22.794986    -48.907617   
1     0.968473    -1.100358    -4.668085    -12.176418    -23.796527   

   Charge_pH_12  Charge_pH_13  Charge_pH_14  
0    -60.178866    -66.546125    -68.693382  
1    -28.944735    -32.552110    -33.818480  

[2 rows x 37 columns]

In [33]:
bashour_results.style

# /\ Approved

In [15]:
# Test Antibody Numbering
print("🔢 Testing Antibody Numbering...")

numbering = AntibodyNumbering(scheme='imgt')
try:
    # Number heavy chain
    heavy_numbered = numbering.number_sequence(HEAVY_SEQUENCE, 'H')  # Use VH portion only
    light_numbered = numbering.number_sequence(LIGHT_SEQUENCE, 'L')  # Use VH portion only

    print(f"  Heavy chain numbered: {len(heavy_numbered)} positions")
    
    # Show first few positions
    print("  First 10 positions:")
    for i, ((pos, ins), aa) in enumerate(heavy_numbered[:10]):
        print(f"    {pos:3d}{ins} {aa}")
    
    # Get CDR sequences
    annotated_H, cdrs_H = numbering.get_cdr_sequences(heavy_numbered, 'H')
    annotated_L, cdrs_L = numbering.get_cdr_sequences(light_numbered, 'L')

except Exception as e:
    print(f"  ⚠️ Numbering failed (may need ANARCI installed): {e}")

🔢 Testing Antibody Numbering...
  Heavy chain numbered: 116 positions
  First 10 positions:
      1  Q
      2  V
      3  Q
      4  L
      5  V
      6  Q
      7  S
      8  G
      9  A
     11  E


In [16]:
cdrs_H, cdrs_L, heavy_numbered, light_numbered, annotated_H, annotated_L

({'cdrh1': 'GGTFSSYA', 'cdrh2': 'IIPIFGTA', 'cdrh3': 'ARSHYGLDY'},
 {'cdrl1': 'HSISSY', 'cdrl2': 'AAS', 'cdrl3': 'QQSYSTPLT'},
 [((1, ' '), 'Q'),
  ((2, ' '), 'V'),
  ((3, ' '), 'Q'),
  ((4, ' '), 'L'),
  ((5, ' '), 'V'),
  ((6, ' '), 'Q'),
  ((7, ' '), 'S'),
  ((8, ' '), 'G'),
  ((9, ' '), 'A'),
  ((11, ' '), 'E'),
  ((12, ' '), 'V'),
  ((13, ' '), 'K'),
  ((14, ' '), 'K'),
  ((15, ' '), 'P'),
  ((16, ' '), 'G'),
  ((17, ' '), 'A'),
  ((18, ' '), 'S'),
  ((19, ' '), 'V'),
  ((20, ' '), 'K'),
  ((21, ' '), 'V'),
  ((22, ' '), 'S'),
  ((23, ' '), 'C'),
  ((24, ' '), 'K'),
  ((25, ' '), 'A'),
  ((26, ' '), 'S'),
  ((27, ' '), 'G'),
  ((28, ' '), 'G'),
  ((29, ' '), 'T'),
  ((30, ' '), 'F'),
  ((35, ' '), 'S'),
  ((36, ' '), 'S'),
  ((37, ' '), 'Y'),
  ((38, ' '), 'A'),
  ((39, ' '), 'I'),
  ((40, ' '), 'S'),
  ((41, ' '), 'W'),
  ((42, ' '), 'V'),
  ((43, ' '), 'R'),
  ((44, ' '), 'Q'),
  ((45, ' '), 'A'),
  ((46, ' '), 'P'),
  ((47, ' '), 'G'),
  ((48, ' '), 'Q'),
  ((49, ' '), 'G'),
  

# /\ Approved

In [17]:
# Test Peptide Descriptor Calculator
print("🧪 Testing Peptide Descriptor Calculator...")

peptide_calc = PeptideDescriptorCalculator()
peptide_results = peptide_calc.calculate_all(
    heavy_sequence=HEAVY_SEQUENCE,
    light_sequence=LIGHT_SEQUENCE
)

print(f"  Calculated descriptors for {len(peptide_results)} chains")
print(f"  Total descriptors per chain: {len(peptide_results.columns)}")


🧪 Testing Peptide Descriptor Calculator...
  Calculated descriptors for 2 chains
  Total descriptors per chain: 9817

  Sample descriptors:


chain                                           sequence  length  \
0  Heavy  QVQLVQSGAEVKKPGASVKVSCKASGGTFSSYAISWVRQAPGQGLE...     446   
1  Light  DIQMTQSPSSLSASVGDRVTITCRASHSISSYLAWYQQKPGKAPKL...     214   

   aliphatic_index     boman  charge_pH7.4  isoelectric_point  \
0        71.591928  1.358004      3.765413           8.321377   
1        67.429907  1.643505      0.375036           7.847862   

   instability_index  molecular_weight  molar_extinction_reduced  ...  \
0          46.153363       48473.79784                       NaN  ...   
1          57.210748       23173.78954                       NaN  ...   

   protpy_apaac_APAAC_72  protpy_apaac_APAAC_73  protpy_apaac_APAAC_74  \
0                  0.802                  0.633                 -1.139   
1                 -0.172                 -0.560                  0.043   

   protpy_apaac_APAAC_75  protpy_apaac_APAAC_76  protpy_apaac_APAAC_77  \
0                  0.633                  0.591                 -0.886   
1                 -0.129                  0.129                  2.543   

   protpy_apaac_APAAC_78  protpy_apaac_APAAC_79  protpy_apaac_APAAC_80  \
0                 -1.941                 -0.169                 -0.211   
1                  0.043                 -3.276                 -2.198   

   hydrophobic_moment_w5_a100  
0                    0.864565  
1                    1.029839  

[2 rows x 9817 columns]

In [34]:
peptide_results.style

In [36]:
import peptides

def get_peptide_profiles(sequence, window=1):
    """
    Compute various per-residue profiles for a peptide sequence.
    
    Parameters:
    -----------
    sequence : str
        The peptide sequence
    window : int
        Window size for profile calculations (default: 1)
    
    Returns:
    --------
    dict : Dictionary containing different profile arrays
    """
    p = peptides.Peptide(sequence)
    profiles = {}
    
    # Common profiles using different scales
    profile_scales = {
        'charge_sign': peptides.tables.CHARGE.get('sign', {}),
        'hydrophobicity_kd': peptides.tables.HYDROPHOBICITY.get('KyteDoolitle', {}),
        'hydrophobicity_hw': peptides.tables.HYDROPHOBICITY.get('HoppWoods', {}),
        'hydrophobicity_cornette': peptides.tables.HYDROPHOBICITY.get('Cornette', {}),
        'hydrophobicity_eisenberg': peptides.tables.HYDROPHOBICITY.get('Eisenberg', {}),
        'hydrophobicity_rose': peptides.tables.HYDROPHOBICITY.get('Rose', {}),
        'hydrophobicity_janin': peptides.tables.HYDROPHOBICITY.get('Janin', {}),
        'hydrophobicity_engelman': peptides.tables.HYDROPHOBICITY.get('Engelman', {}),
    }
    
    for profile_name, scale in profile_scales.items():
        if scale:
            try:
                profiles[profile_name] = p.profile(scale, window=window)
            except:
                profiles[profile_name] = []
    
    return profiles

seq_hyd = "QVQLVQSGAEVKKPGASVKVSCKASGGTFSSYAISWVRQAPGQGLEWMGGIIPIFGTANYAQKFQGRVTITADESTSTAYMELSSLRSEDTAVYYCARSHYGLDYWGQGTLVTVSSASTKGPSVFPLAPSSKSTSGGTAALGCLVKDYFPEPVTVSWNSGALTSGVHTFPAVLQSSGLYSLSSVVTVPSSSLGTQTYICNVNHKPSNTKVDKKVEPKSCDKTHTCPPCPAPELLGGPSVFLFPPKPKDTLMISRTPEVTCVVVDVSHEDPEVKFNWYVDGVEVHNAKTKPREEQYASTYRVVSVLTVLHQDWLNGKEYKCKVSNKALPAPIEKTISKAKGQPREPQVYTLPPSRDELTKNQVSLTCLVKGFYPSDIAVEWESNGQPENNYKTTPPVLDSDGSFFLYSKLTVDKSRWQQGNVFSCSVMHEALHNHYTQKSLSLSPGK"
get_peptide_profiles(seq_hyd)

{'charge_sign': [0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  0.0,
  1.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  -1.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  0.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  -1.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  -1.0,
  -1.0,
  -1.0,
  0.0,
  1.0,
  0.0,
  1.0,
  -1.0,
  0.0,
  0.0,
  -1.0,
  -1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  

In [18]:
peptide_results.style

# /\ Approved

## 5. Sequence-based Analysis {#sequence}

Now let's test the main AntibodyDescriptorCalculator with sequence-only analysis.

In [19]:
# Initialize main calculator
print("🚀 Initializing AntibodyDescriptorCalculator...")



calc = AntibodyDescriptorCalculator(config=custom_config)
print("✅ Calculator initialized successfully")

# Check calculator status
if hasattr(calc, 'get_calculator_status'):
    status = calc.get_calculator_status()
    print("\n📋 Calculator Status:")
    for category, calculators in status.items():
        if category != 'external_tools':
            print(f"  {category}:")
            for calc_name, calc_info in calculators.items():
                enabled = "✅" if calc_info.get('enabled', False) else "⚪"
                print(f"    {enabled} {calc_name}: {calc_info.get('description', '')}")

🚀 Initializing AntibodyDescriptorCalculator...


reduce not found at reduce
Missing external tools: reduce
Some analyses may not be available


✅ Calculator initialized successfully


In [20]:
# Run sequence-only analysis
print("🧬 Running sequence-based analysis...")

sequence_results = calc.calculate_sequence_descriptors(
    heavy_sequence=HEAVY_SEQUENCE,
    light_sequence=LIGHT_SEQUENCE,
    sequence_id="TestAb_Sequence"
)


🧬 Running sequence-based analysis...


Failed to calculate pseudo amino acid composition for sequence
Failed to calculate amphiphilic pseudo amino acid composition for sequence

KeyboardInterrupt



In [ ]:
sequence_results = sequence_results.drop(["H", "L","Peptide_molar_extinction_reduced", "Peptide_molar_extinction_cystines"], axis = 1)
print(f"✅ Sequence analysis completed!")
print(f"   Results shape: {sequence_results.shape}")
print(f"   Columns: {len(sequence_results.columns)}")

In [ ]:
# list of charge cols
charge_cols = [f"Heavy_Charge_pH_{i}" for i in range(1, 15)]

# drop if they already exist
sequence_results = sequence_results.drop(columns=charge_cols, errors="ignore")

# expand the dictionary
charges_expanded = sequence_results["Heavy_Charges (all pH values)"].apply(pd.Series)
charges_expanded.columns = [f"Heavy_Charge_pH_{c}" for c in charges_expanded.columns]

# merge back
sequence_results = pd.concat([sequence_results.drop(columns=["Heavy_Charges (all pH values)"]),
                             charges_expanded], axis=1)

# list of charge cols
charge_cols = [f"Light_Charges_pH_{i}" for i in range(1, 15)]

# drop if they already exist
sequence_results = sequence_results.drop(columns=charge_cols, errors="ignore")

# expand the dictionary
charges_expanded = sequence_results["Light_Charges (all pH values)"].apply(pd.Series)
charges_expanded.columns = [f"Light_Charges_pH_{c}" for c in charges_expanded.columns]

# merge back
sequence_results = pd.concat([sequence_results.drop(columns=["Light_Charges (all pH values)"]),
                             charges_expanded], axis=1)

liabilities = sequence_results[["SeqID", "Type", "Heavy_Length", "Light_Length", "liabilities"]]

In [ ]:
sequence_results = sequence_results.drop("liabilities", axis = 1)
sequence_results

In [ ]:
liabilities

## 6. Structure-based Analysis {#structure}

If a PDB file is available, let's test structure-based analysis.

In [21]:
# Initialize main calculator
print("🚀 Initializing AntibodyDescriptorCalculator...")



calc = AntibodyDescriptorCalculator(config=custom_config)
print("✅ Calculator initialized successfully")

# Check calculator status
if hasattr(calc, 'get_calculator_status'):
    status = calc.get_calculator_status()
    print("\n📋 Calculator Status:")
    for category, calculators in status.items():
        if category != 'external_tools':
            print(f"  {category}:")
            for calc_name, calc_info in calculators.items():
                enabled = "✅" if calc_info.get('enabled', False) else "⚪"
                print(f"    {enabled} {calc_name}: {calc_info.get('description', '')}")

🚀 Initializing AntibodyDescriptorCalculator...


reduce not found at reduce
Missing external tools: reduce
Some analyses may not be available


✅ Calculator initialized successfully


In [22]:
# Check if PDB file exists
if PDB_FILE.exists():
    print(f"📁 Found PDB file: {PDB_FILE}")
    pdb_available = True
else:
    print(f"⚠️ PDB file not found at: {PDB_FILE}")
    print("   Structure-based analysis will be skipped.")
    print("   Please place your test.pdb file in the data/test directory.")
    pdb_available = False

print(f"\n🏗️ Structure analysis available: {pdb_available}")

📁 Found PDB file: /home/HX46_FR5/repo_perso/AbXtract/examples/data/test/test.pdb

🏗️ Structure analysis available: True


In [23]:
# Run structure analysis if PDB is available
structure_results, df_residues = calc.calculate_structure_descriptors(
    pdb_file=PDB_FILE,
    structure_id="TestAb_Structure"
)

@> 1818 atoms and 1 coordinate set(s) were parsed in 0.02s.
DSSP analysis failed: DSSP failed to produce an output


In [24]:
# just Arpeggio JSON output not found in /var/tmp/tmpx83mx7h2


In [25]:
structure_results_seq = structure_results[['disulfide_bonds',
'residue_sap',
'high_sap_residues',
'residue_sasa',
'sidechain_sasa',
'relative_sasa',
'buried_residues',
"residue_pka",
"pka_shifts",
"charge_profile",
"stability_profile"
]]
structure_results_seq

disulfide_bonds  \
0  [{'cys1': 'H_21', 'cys2': 'H_95', 'distance': ...   

                                         residue_sap  \
0  {'ASP_0_H': 0.029531839957845273, 'VAL_1_H': 0...   

                                   high_sap_residues  \
0  [LEU_10_H, PRO_40_H, TYR_58_H, LEU_101_H, TYR_...   

                                        residue_sasa  \
0  {'ASP_0_H': {'N': 40.450005754993995, 'CA': 9....   

                                      sidechain_sasa relative_sasa  \
0  {'ASP_0_H': 111.79910841184281, 'VAL_1_H': 31....            {}   

                                     buried_residues  \
0  [LEU_3_H, GLU_5_H, LEU_19_H, CYS_21_H, VAL_28_...   

                                         residue_pka  \
0  0    {'ASP_54_H': 2.55, 'ASP_61_H': 2.76, 'ASP...   

                                          pka_shifts  \
0  0    {'ASP_54_H': -1.25, 'ASP_61_H': -1.04, 'A...   

                                      charge_profile  \
0  0    {0.0: {'folded': 11.99, 'unfolded': 12.0}...   

                                   stability_profile  
0  0    {0.0: 11.82, 1.0: 11.76, 2.0: 11.18, 3.0:...

In [26]:
df_residues

Residue_Type  Residue_Number Chain    pKa Buried ratio  \
0            N+               0     H   7.84            0   
1           GLU               5     H   5.16            0   
2           ARG              18     H  12.36            0   
3           CYS              21     H  99.99           50   
4           TYR              32     H  10.75            0   
5           ARG              37     H  14.66           16   
6           LYS              42     H  10.43           53   
7           GLU              43     H   4.63            0   
8           ARG              44     H   8.04           31   
9           GLU              45     H   3.43            0   
10          ASP              54     H   2.55            0   
11          HIS              55     H   5.89            0   
12          TYR              58     H  10.30            3   
13          TYR              59     H  10.50            0   
14          ASP              61     H   2.76            0   
15          LYS              64     H  11.49            0   
16          ARG              66     H  13.45            0   
17          ARG              71     H  10.80           40   
18          ASP              72     H   2.57            0   
19          LYS              75     H  10.84           80   
20          TYR              79     H   9.94            8   
21          ARG              86     H  12.21            0   
22          GLU              88     H   4.22            0   
23          ASP              89     H   2.29            0   
24          TYR              93     H  12.28            0   
25          TYR              94     H  10.47            0   
26          CYS              95     H  99.99            0   
27          ARG              97     H  12.35            0   
28          ASP              99     H   4.10           62   
29          GLU             102     H   4.70           55   
30          TYR             103     H  10.03           22   
31          TYR             104     H  10.06           40   
32          TYR             105     H  10.20            0   
33          ASP             108     H   3.56           25   
34           C-             120     H   2.87            0   

   Disolvation regular Cst Disolvation regular Nb Effects RE Cst Effects RE Nb  
0                     0.35                    197           0.00             0  
1                     0.19                    152           0.00             0  
2                     0.52                    211           0.00             0  
3                     2.32                    421           0.39             0  
4                     0.32                    267           0.00             0  
5                     0.83                    326           0.11             0  
6                     2.38                    430           0.69             0  
7                     0.11                    161           0.00             0  
8                     1.04                    367           0.06             0  
9                     0.48                    261           0.00             0  
10                    0.12                    148           0.00             0  
11                    0.33                    131           0.00             0  
12                   -0.43                    289           0.00             0  
13                    0.00                      0           0.00             0  
14                    0.00                      0           0.00             0  
15                    0.51                    253           0.00             0  
16                    0.17                    210           0.00             0  
17                    1.82                    394           0.00             0  
18                    0.44                    275           0.00             0  
19                    3.20                    505           0.00             0  
20                    0.59                    305           0.00             0  
21                    0.

In [30]:
 structure_results_comp= structure_results.drop(['disulfide_bonds',
'residue_sap',
'high_sap_residues',
'residue_sasa',
'sidechain_sasa',
'relative_sasa',
'buried_residues',
"residue_pka",
"pka_shifts",
"charge_profile",
"stability_profile",
"secondary_structure",
"ss_composition"], axis = 1)
    
import pandas as pd
import re
import numpy as np


def extract_second_number(value):
    """
    Aggressively extract the second number from messy strings like:
    '0 5.21 Name: pI_folded, dtype: float64'
    
    Returns just 5.21
    """
    # Handle Series objects (extract first value)
    if isinstance(value, pd.Series):
        if len(value) > 0:
            value = value.iloc[0]
        else:
            return np.nan
    
    # Handle NaN values
    if value is None or (isinstance(value, float) and np.isnan(value)):
        return np.nan
    
    # Convert to string
    value_str = str(value)
    
    # Find all numbers (including negative and decimals)
    # This regex captures integers and floats
    numbers = re.findall(r'-?\d+\.?\d*', value_str)
    
    # Convert strings to floats
    try:
        if len(numbers) >= 2:
            # Return the second number (index 1)
            return float(numbers[1])
        elif len(numbers) == 1:
            # If only one number, return it
            return float(numbers[0])
        else:
            return np.nan
    except (ValueError, IndexError):
        return np.nan

# Method 1: Clean columns that need it
df_cleaned = structure_results_comp.copy()

# First, identify which columns need cleaning
columns_to_clean = []
for col in df_cleaned.columns:
    # Sample the first non-null value
    sample_val = df_cleaned[col].dropna().head(1)
    if not sample_val.empty:
        sample_str = str(sample_val.iloc[0])
        if 'Name:' in sample_str or 'dtype:' in sample_str:
            columns_to_clean.append(col)


# Clean the identified columns
for col in columns_to_clean:
    df_cleaned[col] = df_cleaned[col].apply(extract_second_number)

structure_results_comp = df_cleaned.copy()


In [31]:
structure_results_comp.style